In [1]:
%%time
# Importing all the necessary libraries for this project.

import pandas as pd
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from pylab import rcParams
import pandas as pd
from bs4 import BeautifulSoup
import requests
import json

CPU times: user 1.43 s, sys: 489 ms, total: 1.92 s
Wall time: 2.48 s


In [2]:
pd.set_option('display.max_colwidth', -1)
pd.set_option('display.max_columns', None)

In [3]:
rawdata = pd.read_json("https://s3.amazonaws.com/temp-data-pulls/newdump.json")

In [4]:
## USING ONLY PIN & BLOG POSTS - RAW DATA HERE

pd.options.mode.chained_assignment = None
rawpin_blog = rawdata[(rawdata["type"]=="pin") | (rawdata["type"]=="blog post")]
rawpin_blog.drop(["has_spend"], axis = 1, inplace=True)

In [5]:
# SEPARATING OUT THE COLUMNS

channel_info = rawpin_blog['channel_info'].apply(pd.Series)
channel_info.columns = ["channel", "info"]

In [6]:
# SEPARATING OUT THE COLUMNS THE CONTENT_INFO COLUMN

content_info = rawpin_blog['content'].apply(pd.Series)
content_info.drop(['author_email', 'content', 'pinned_from'], axis=1, inplace=True) ## THESE HAVE ONLY NULLS

In [7]:
# FIX NAN VALUES IN EACH COLUMN THAT CONTAINS COUNT

for x in content_info.columns:
    if "count" in x:
        content_info[x].fillna(np.NaN, inplace = True)

In [8]:
# JOINING THE DATASETS ONTO THE RAW

master_pinblog = rawpin_blog.join(channel_info).join(content_info)
master_pinblog.drop(['channel_info', 'content'], axis = 1, inplace = True)

In [9]:
master_pinblog.columns = ['brand', 'engagement', 'uniqueid', 'impact', 'share_token', 'timestamp',
       'type', 'urls', 'channel', 'info', 'author_name', 'comment_count',
       'description', 'fb_likecount', 'fb_sharecount',
       'gplus_count', 'hashtags', 'image_url', 'like_count',
       'link', 'linkedin_sharecount', 'links', 'pin_id', 'pin_url',
       'pin_count', 'post_type', 'repin_count', 'summary',
       'thumbnail_url', 'title', 'tweet_count']

master_pinblog["links_count"] = master_pinblog['links'].str.len()

In [10]:
master_pinblog[master_pinblog["channel"] == "blog"].head(5)

brand  engagement                                    uniqueid    impact  \
141  137316  33          MTM3MzE2LTIwMTQ2MTUyX2Jsb2cgcG9zdF8xNzQ4Mw  0.057249   
142  137322  1           MTM3MzIyLTIwMTQ0MDE0X2Jsb2cgcG9zdF8xNzQ4Mw  0.000927   
175  137329  1077        MTM3MzI5LTIwMTQ0NzQ2X2Jsb2cgcG9zdF8xNzQ4Mw  2.625943   
242  137322  1           MTM3MzIyLTIwMTQ0MDE1X2Jsb2cgcG9zdF8xNzQ4Mw  0.000937   
244  137329  3           MTM3MzI5LTIwMTQ0NzQ3X2Jsb2cgcG9zdF8xNzQ4Mw  0.006514   

                                     share_token           timestamp  \
141  MUEF3US5L1fQ9o23xiryJN3K85bXD5n2I0Md_RII3LY 2017-11-16 02:00:00   
142  B0yFf6kIDBS9-poQ1Fyv2t3K85bXD5n2I0Md_RII3LY 2017-11-16 02:00:00   
175  jByu9k_eNjDs0NyPjDTqvt3K85bXD5n2I0Md_RII3LY 2017-11-16 01:05:28   
242  2l5jpXZ34bmotrXo0V_z1t3K85bXD5n2I0Md_RII3LY 2017-11-15 23:44:52   
244  HUE4eXJv3ImpRfBokd2d5N3K85bXD5n2I0Md_RII3LY 2017-11-15 23:39:41   

          type  \
141  blog post   
142  blog post   
175  blog post   
242  blog post   
244  blog post   

                                                                                                                                                                                                                                                                                                                                        urls  \
141  [{'url': 'https://www.glamour.com/story/riverdale-season-2-episode-6-recap-who-is-the-sugar-man', 'path': '/story/riverdale-season-2-episode-6-recap-who-is-the-sugar-man', 'hostname': 'www.glamour.com', 'utm': {'term': None, 'medium': None, 'campaign': None, 'content': None, 'source': None, 'id': None}}]                         
142  [{'url': 'https://www.teenvogue.com/story/riverdale-recap-season-2-episode-6', 'path': '/story/riverdale-recap-season-2-episode-6', 'hostname': 'www.teenvogue.com', 'utm': {'term': None, 'medium': None, 'campaign': None, 'content': None, 'source': None, 'id': None}}]                                                               
175  [{'url': 'https://www.wmagazine.com/story/leonardo-da-vinci-salvator-mundi-painting-sells-for-record-price', 'path': '/story/leonardo-da-vinci-salvator-mundi-painting-sells-for-record-price', 'hostname': 'www.wmagazine.com', 'utm': {'term': None, 'medium': None, 'campaign': None, 'content': None, 'source': None, 'id': None}}]   
242  [{'url': 'https://www.teenvogue.com/story/madelaine-petsch-danielle-campbell-f-the-prom-trailer', 'path': '/story/madelaine-petsch-danielle-campbell-f-the-prom-trailer', 'hostname': 'www.teenvogue.com', 'utm': {'term': None, 'medium': None, 'campaign': None, 'content': None, 'source': None, 'id': None}}]                         
244  [{'url': 'https://www.wmagazine.com/story/get-out-comedy-drama-jordan-peele-golden-globes', 'path': '/story/get-out-comedy-drama-jordan-peele-golden-globes', 'hostname': 'www.wmagazine.com', 'utm': {'term': None, 'medium': None, 'campaign': None, 'content': None, 'source': None, 'id': None}}]                                     

    channel info        author_name  comment_count description  fb_likecount  \
141  blog    []   Christopher Rosa  NaN             NaN         28.0           
142  blog    []   Jessica MacLeish  NaN             NaN         0.0            
175  blog    []   Marissa G. Muller NaN             NaN         982.0          
242  blog    []   Suzannah Weiss    NaN             NaN         0.0            
244  blog    []   Brooke Marine     NaN             NaN         2.0            

     fb_sharecount  gplus_count hashtags image_url  like_count  \
141  5.0            0.0          NaN      NaN      NaN           
142  1.0            0.0          NaN      NaN      NaN           
175  95.0           0.0          NaN      NaN      NaN           
242  1.0            0.0          NaN      NaN      NaN           
244  1.0            0.0          NaN      NaN      NaN           

                                                                                  

In [11]:
# create new df called blogs that only contains blogs
blogs = master_pinblog[master_pinblog.type == 'blog post']
# converts link to string so we can split
blogs.link = blogs.link.astype(str)
# instantiate a new list called new_mag
new_mag = []
# list comprehension that just keeps part before ‘.com’
# we can use list comprehension because this is true for all values
magazine = [i.split('.com')[0] for i in blogs.link]
# start for loop to get rid of everything before the name of the magazine
for i in magazine:
    if '.' in i:
        new_mag.append(i.split('.')[1])
# if there isn’t a ‘.’ it just sends the existing name to the list
    else:
        new_mag.append(i)
# create new column for the df with the publications
blogs['pub'] = new_mag
print(blogs.pub.unique())

['glamour' 'teenvogue' 'wmagazine' 'allure' 'cntraveler'
 'architecturaldigest' 'vogue']


In [42]:
def scraper_links(url):
    article = ""
    domain = url.split()[1]
    url = url.split()[0]
    print(url)
    
    ## TRY TO SEE IF THE LINK EXISTS. ELSE JUST RETURN NONE AND MOVE ON.
    try:
        request = requests.get(url)
        soup = BeautifulSoup(request.text, "lxml")
        info = json.loads(soup.find('script', type='application/ld+json').text)
    except:
        article = "Link is Dead"
        other_info = {'headline': None, 'image': None, 'description': None, 'keywords': None, '@type': None}
        return(article, other_info)

    ## IF LINK WORKS, USE JSON ELSE USE BEAUTIFUL SOUP TO GET DATA.
    try:
        article = info["articleBody"]
    except:
        try:
            if domain == "glamour":
                for posts in soup.find_all('div', {'class' : 'article__content'}):
                    article = posts.text
            elif domain == "teenvogue":
                for posts in soup.find_all('div', {'class' : 'content article-content'}):
                    article = posts.text
            elif domain == "wmagazine":
                for posts in soup.find_all('div', {'class' : 'body-text'}):
                    article = posts.text
            elif domain == "allure":
                for posts in soup.find_all('div', {'class' : 'article-body'}):
                    article = posts.text
            elif domain == "cntraveler":
                for posts in soup.find_all('div', {'class' : 'article-body'}):
                    article = posts.text
            elif domain == "architecturaldigest":
                for posts in soup.find_all('div', {'class' : 'article-content-main'}):
                    article = posts.text
            elif domain == "vogue":
                for posts in soup.find_all('div', {'class' : 'article-copy--body'}):
                    article = posts.text
        except:
            article = "Article Not Found"

            
    ## USE JSON TO EXTRACT IMAGE INFO & OTHER STUFF ELSE RETURN NONE
    
    try:        
        attributes = { 'headline', 'image', 'description', 'keywords', '@type'}
        other_info = { k:v for k,v in info.items() if k in attributes }
    except:
        other_info = { 'headline': None, 'image': None, 'description': None, 'keywords': None, '@type': None}
   

    return(article, other_info)

In [43]:
blogs.reset_index(drop=True, inplace=True)
blogs["links + pub"] = blogs['link'] + str(" ") + blogs['pub']

In [44]:
%%time
blogs["story"] = blogs["links + pub"].apply(scraper_links)

https://www.glamour.com/story/riverdale-season-2-episode-6-recap-who-is-the-sugar-man
https://www.teenvogue.com/story/riverdale-recap-season-2-episode-6
https://www.wmagazine.com/story/leonardo-da-vinci-salvator-mundi-painting-sells-for-record-price
https://www.teenvogue.com/story/madelaine-petsch-danielle-campbell-f-the-prom-trailer
https://www.wmagazine.com/story/get-out-comedy-drama-jordan-peele-golden-globes
https://www.glamour.com/story/dakota-johnson-and-chris-martin-are-reportedly-dating
https://www.allure.com/story/blake-shelton-homophobic-racist-tweets-people-sexiest-man-alive-2017
https://www.allure.com/story/time-for-sexiest-man-alive-title-to-die
https://www.wmagazine.com/story/pharrell-song-that-wont-be-released-for-100-years-climate-change
https://www.teenvogue.com/story/milk-vines-viral-white-mediocrity
https://www.glamour.com/story/jennifer-lawrence-says-job-was-threatened-after-she-stuck-up-for-herself-against-director
https://www.allure.com/story/too-faced-better-than

https://www.glamour.com/story/this-is-us-season-2-episode-8-recap-we-need-to-talk-about-kevin
https://www.wmagazine.com/gallery/people-sexiest-men-alive-who-arent-blake-shelton
https://www.cntraveler.com/story/on-the-rise-inside-sao-paulos-youth-driven-revival
https://www.cntraveler.com/gallery/the-look-of-a-hip-new-sao-paulo
https://www.wmagazine.com/story/abc-luc-besson-and-jean-dujardin-make-french-crime-procedural
https://www.glamour.com/story/lilly-singh-pantene-spokeswoman
https://www.allure.com/story/white-woman-transracial-filipino-identity
https://www.teenvogue.com/story/me-too-march-hollywood
https://www.allure.com/story/jaclyn-friedman-unscrewed-book-sexual-pleasure
https://www.teenvogue.com/story/best-black-friday-sales-to-shop
https://www.teenvogue.com/story/christian-louboutin-launches-signature-capsule-collection
https://www.teenvogue.com/story/oreo-cookies-and-creme-candy-canes
https://www.allure.com/story/maybelline-releasing-more-master-chrome-highlighter-shades
https

https://www.glamour.com/story/gigi-hadid-glamour-women-of-the-year-awards-2017-speech
https://www.cntraveler.com/story/how-to-avoid-thanksgiving-traffic-according-to-google
https://www.cntraveler.com/story/flight-deal-boston-to-peru-from-389-round-trip
https://www.wmagazine.com/story/serena-williams-first-public-outing-gigi-hadid
https://www.glamour.com/story/nicole-kidman-glamour-women-of-the-year-awards-2017
https://www.cntraveler.com/story/travel-specialists-we-trust
https://www.glamour.com/story/maxine-waters-impeach-chant-2017-women-of-the-year-awards
https://www.glamour.com/story/serena-williams-first-appearance-since-giving-birth-woty
https://www.glamour.com/story/lynda-carter-presents-patty-jenkins-woman-of-the-year-award
https://www.wmagazine.com/story/patty-jenkins-pays-tribute-to-lynda-carter
https://www.teenvogue.com/story/camila-cabello-exposed-bra-inserts-mtv-emas
https://www.glamour.com/story/me-too-stories-glamour-women-of-the-year-awards-2017
https://www.cntraveler.com

https://www.teenvogue.com/story/how-to-network-for-internships
https://www.allure.com/story/dry-brushing-a-quick-way-to-smooth-skin
https://www.glamour.com/story/women-of-the-year-2017-summit-live-blog
https://www.glamour.com/gallery/gigi-hadid-maybelline-lipsticks-review
https://www.teenvogue.com/story/tiffany-trump-nude-sheer-dress-instagram-dinner
https://www.teenvogue.com/story/feeling-lost-in-college
https://www.teenvogue.com/story/microinvalidations-are-real
https://www.glamour.com/story/cyber-monday-deals
https://www.cntraveler.com/story/how-to-find-a-vacation-rental-for-thanksgiving
https://www.cntraveler.com/story/germanys-train-of-the-future-includes-spin-bikes-and-big-screen-tvs
https://www.cntraveler.com/story/what-all-those-numbers-and-letters-on-your-boarding-pass-really-mean
https://www.cntraveler.com/story/inside-emirates-new-first-class-suites
https://www.cntraveler.com/story/why-the-danish-town-of-aabenraa-refuses-to-change-its-name
https://www.cntraveler.com/story/th

https://www.wmagazine.com/story/melania-trump-european-outfits-asia-trip-america-first
https://www.teenvogue.com/story/milly-michelle-smith-planned-parenthood-shirt-donald-trump-election
https://www.glamour.com/story/career-late-bloomers
https://www.teenvogue.com/story/ellen-page-brett-ratner-sexual-harassment
https://www.glamour.com/story/ellen-page-brett-ratner-sexually-harassed-outed-her-facebook
https://www.teenvogue.com/story/what-to-watch-on-netflix-thanksgiving
https://www.wmagazine.com/story/ellen-page-says-brett-ratner-outed-her
https://www.allure.com/story/racist-native-american-makeup-tutorial-parody
https://www.glamour.com/story/kourtney-kardashian-lob-haircut
https://www.teenvogue.com/story/maddie-ziegler-9-impressions
https://www.allure.com/story/needle-lashes-instagram
https://www.wmagazine.com/story/louis-ck-these-stories-are-true
https://www.teenvogue.com/story/take-instagram-photos-on-this-russian-companys-private-jet
https://www.wmagazine.com/story/eminem-beyonce-son

...

http://www.vogue.com/13385039/jose-ignacio-uruguay-travel-guide-secret-beach-private-island/
http://www.vogue.com/13385453/the-row-new-shoe-collection-manhattan-store/
http://www.wmagazine.com/fashion/news-gossip-roundup/2016/01/90-supermodels-reunite/
http://www.vogue.com/13384230/beautiful-bathrooms-interior-design-vogue/
http://www.vogue.com/slideshow/13385473/best-bathrooms-in-vogue/
http://www.teenvogue.com/gallery/under-the-radar-makeup-palettes
http://www.vogue.com/13385523/david-bowie-blackstar-famous-men-who-wore-makeup-elvis-mick-jagger/
http://www.vogue.com/13385566/kanye-west-real-friends/
http://www.teenvogue.com/gallery/reality-tv-stars
http://www.vogue.com/13385541/remembering-andre-courreges/
http://www.teenvogue.com/gallery/fitness-apps-all-fitness-levels
http://www.teenvogue.com/story/kendall-jenner-2016-trends
http://www.wmagazine.com/beauty/beauty-insiders/2016/01/big-girl-talk-with-gucci-westman/
http://www.vogue.com/13385366/david-bowie-fashion-influence-runway-bi

http://www.teenvogue.com/story/taylor-swift-making-of-blank-space
http://www.teenvogue.com/gallery/unicorn-hair-color-ideas
http://www.teenvogue.com/gallery/long-haircut-ideas
http://www.teenvogue.com/story/adele-gym-selfie
http://www.teenvogue.com/story/advice-friendship-communication-arabelle-sicardi
http://www.teenvogue.com/story/brian-encinia-indicted-sandra-bland-case
http://www.teenvogue.com/story/justin-bieber-hailey-baldwin-meeting
http://www.vogue.com/slideshow/13383602/lauren-schwab-and-bobby-webster-wedding/
http://www.vogue.com/13384686/weddings-lauren-schwab-bobby-webster-east-hampton-longhouse-reserve/
http://www.teenvogue.com/gallery/gigi-hadid-white-jeans-winter
http://www.teenvogue.com/gallery/fuller-house-stills
http://www.vogue.com/13384535/most-romantic-paris-restaurants/
http://www.allure.com/beauty-trends/blogs/daily-beauty-reporter/2016/01/shay-mitchell-peoples-choice-awards-beauty.html
http://www.vogue.com/13384853/best-new-age-beauty-products/
http://www.teenvo

http://www.allure.com/beauty-trends/blogs/daily-beauty-reporter/2016/01/karrueche-tran-makeup-collection.html
http://www.vogue.com/13384736/eddie-redmayne-burberry-golden-globes-red-carpet-menswear/
http://www.vogue.com/13384660/bella-hadid-rosy-makeup-pink-blush-tinted-lip-balm/
http://www.teenvogue.com/story/chipotle-federal-investigation-norovirus-outbreak
http://www.vogue.com/13384689/wedding-rules-to-break/
http://www.teenvogue.com/gallery/how-eleven-makeup-artists-made-it-big
http://www.vogue.com/13384731/making-a-murderer-free-steven-avery-brendan-dassey/
http://www.teenvogue.com/gallery/grace-hartzel-mmk-campaign
http://www.teenvogue.com/story/zayn-malik-grandmother-tribute
http://www.allure.com/beauty-trends/blogs/daily-beauty-reporter/2016/01/target-nail-polish-line-reality-shows.html
http://www.allure.com/beauty-trends/blogs/daily-beauty-reporter/2016/01/kendall-jenner-skin-care-routine.html
http://www.teenvogue.com/story/miami-city-ballet-debuts-why-we-dance-film
http://www

http://www.wmagazine.com/people/celebrities/2016/01/best-performances-hollywood-actors-award-season/
http://www.teenvogue.com/story/taylor-swift-wildest-dreams-performance
http://www.allure.com/beauty-trends/blogs/daily-beauty-reporter/2016/01/easy-waves-tutorial.html
http://www.teenvogue.com/story/getting-back-into-fitness-routine-new-year
http://www.teenvogue.com/story/coachella-2016-set-list
http://www.teenvogue.com/story/zayn-malik-gigi-hadid-snapchat
http://www.vogue.com/slideshow/13381919/luke-edward-hall-house-tour-photos/
http://www.vogue.com/13381930/luke-edward-hall-interior-design-whimsical-house-tour-london-antiques/
http://www.vogue.com/13384194/deepika-padukone-bollywood-star-style/
http://www.cntraveler.com/galleries/2016-01-05/when-the-runway-makes-us-want-to-travel
http://www.vogue.com/13384213/best-celebrity-hair-makeup-ideas-taylor-swift-rihanna/
http://www.vogue.com/slideshow/13384199/10-best-beauty-looks-suki-waterhouse-taylor-swift-rihanna/
http://www.cntraveler.c

http://www.vogue.com/13383582/tv-film-trends-2016/
http://www.allure.com/beauty-trends/blogs/daily-beauty-reporter/2016/01/paprika-skin-care-benefits.html
http://www.teenvogue.com/story/movies-in-2016
http://www.teenvogue.com/gallery/one-direction-boys-fashion
http://www.teenvogue.com/story/miley-cyrus-liam-hemsworth-back-together-australia
http://www.vogue.com/13383600/hotels-spa-vacation-retreat-classic-hollywood-star/
http://www.wmagazine.com/people/insiders/2016/01/monse-laura-kim-fernando-garcia/
http://www.teenvogue.com/gallery/monday-morning-beauty-products
http://www.vogue.com/13383598/rihanna-5-things-you-didnt-know/
http://www.vogue.com/13382848/celebrity-kids-new-models/
http://www.teenvogue.com/story/fda-ban-teens-indoor-tanning
http://www.vogue.com/13383985/best-beauty-instagrams-ciara-north-west/
http://www.cntraveler.com/stories/2015-12-31/tom-frestons-lifelong-love-for-india
http://www.teenvogue.com/story/gigi-hadid-cat-shirtless-zayn-instagram
http://www.allure.com/bea

In [48]:
blogs = blogs.join(blogs['story'].apply(pd.Series))
blogs.drop(['story', 'links + pub'], axis=1, inplace = True)

In [57]:
blogs.columns.values[-1] = 'blogdetails'
blogs.columns.values[-2] = 'blogpost'

In [60]:
blogs.to_csv('BlogMaster.csv', mode='a', header=True)